In [26]:
import pandas as pd
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader


In [10]:
from tqdm import tqdm

### Gumawa ng raw dataset dictionary para icompile ang train, test, and val set na csv mula sa file


In [2]:
# iconvert ang bawat csv into a Dataframe

raw_dataset = {
    'train' : pd.read_csv('../new-dataset/train_data.csv').reset_index(drop=True),
    'test' : pd.read_csv('../new-dataset/test_data.csv').reset_index(drop=True),
    'val' : pd.read_csv('../new-dataset/val_data.csv').reset_index(drop=True)
}

In [3]:
raw_dataset

{'train':         ID                                               Text  Age  Gender  \
 0        1  sarap mambully netong mga bobong gen z pota HA...    1       0   
 1        2  TANGINA NG PINALIT NG KAPATID KO KAY ATE. ANG ...    0       1   
 2        4  tangina ng mga straight cis girls na walang al...    0       1   
 3        5  hanggang ngayon, na bebwesit pa rin ako don sa...    1       0   
 4        6  no hate but these aetas should just stay in th...    0       0   
 ...    ...                                                ...  ...     ...   
 1255  2094                   bakla anong ginawa mo pakshet ka    0       1   
 1256  2097                                kupal na bakla haha    0       1   
 1257  2098  sa pinapakitang mong yan insecure ka sakin hah...    0       0   
 1258  2099  Kausapin ka at makikinig ka? Pakamatay kana ha...    0       0   
 1259  2100  hahaha! Kadiri yang mga batang yan! Totoo nama...    1       0   
 
       Physical  Race  Religion  Others  

In [52]:
### Para maaccess ang dataframe for a particular set, use the dictionary keys as an index
raw_dataset['train']
raw_dataset['test']
raw_dataset['val']

ID                                               Text  Age  Gender  \
0      16  TANGINA MO POKPOK!!! WHORE!!! CUNT!!! CHEATER!...    0       1   
1      21         oh god kulot, mukhang aeta si ate HAHAHAHA    0       0   
2      26  eto yung sinasabi kong nakakaputangina na mga ...    0       0   
3      52  Kanser na sa lipunan karamihan ng mga Bisaya n...    0       0   
4      68  Kailan ba mawawala mga bisakol mag maneho nang...    0       0   
..    ...                                                ...  ...     ...   
205  2067  Wag kang mag mataas Kung maitim ka pangit ka R...    0       0   
206  2086  aba putangina hanggang japan ayaw magpaawat ng...    0       0   
207  2089  PUTANGINA KONTI NALANG BABASAGIN KO NA MGA PEL...    1       0   
208  2091  TAPOS NAGPAPALUSOT KA PA NUNG TINANONG KUNG BA...    0       0   
209  2095  Nasobrahan ka yata sa self-love. Ang taba mo n...    0       0   

     Physical  Race  Religion  Others  
0           1     0         0       0  
1           1     1         0       0  
2           0     0         1       0  
3           0     1         0       0  
4           0     1         0       0  
..        ...   ...       ...     ...  
205         1     0         0       0  
206         0     1         0       0  
207         0     0         0       0  
208         1     0         0       0  
209         1     0         0       0  

[210 rows x 8 columns]

In [5]:
# Para mag-access ng isang row sa particular set, gamitin ang iloc or index location
sample_data = raw_dataset['train'].iloc[0]
sample_data

ID                                                          1
Text        sarap mambully netong mga bobong gen z pota HA...
Age                                                         1
Gender                                                      0
Physical                                                    0
Race                                                        0
Religion                                                    0
Others                                                      0
Name: 0, dtype: object

In [8]:
# Para kunin yung text
sample_text = sample_data['Text']
sample_text

'Wala ka na ngang pakinabang, bobo ka pang salot ka. Manang-mana ka sa tatay mong salot.'

In [6]:
# Para kunin yung labels
LABELS = ['Age', 'Gender', 'Physical', 'Race', 'Religion', 'Others']
sample_labels = sample_data[LABELS]
sample_labels

Age         1
Gender      0
Physical    0
Race        0
Religion    0
Others      0
Name: 0, dtype: object

Try natin gumawa ng loop para kunin lahat ng data sa lahat ng sets

In [10]:
for set in raw_dataset.values(): # sa bawat set na meron sa dataset (train, test, val)
    for index, data in set.iterrows(): # use iterrows to iterrate through the rows instead of getting the headers
        print(data)

"""

ang iterrows() ay nagrereturn ng tuple containing the index and data in the set

"""

ID                                                       1829
Text        Wala ka na ngang pakinabang, bobo ka pang salo...
Age                                                         1
Gender                                                      0
Physical                                                    0
Race                                                        0
Religion                                                    0
Others                                                      1
Name: 0, dtype: object
ID                                                       1095
Text        kaya never talaga akong nanuod ng mga anime na...
Age                                                         0
Gender                                                      0
Physical                                                    0
Race                                                        1
Religion                                                    0
Others                                         

'\n\nang iterrows() ay nagrereturn ng tuple containing the index and data in the set\n\n'

Imbis na iprint ang laman ng dataset, try nating iencode siya at gumawa ng panibagong encoded dataset

In [7]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('gklmip/bert-tagalog-base-uncased')

d:\Repo\Thesis\BERT-MLTHSC\venv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [8]:
def encode_data(data):
    text = data["Text"]

    encoding = tokenizer.encode_plus(
        text,
        add_special_tokens=True,
        return_tensors='pt',
        padding='max_length',
        truncation=True,
        max_length=128,
        return_token_type_ids=False,
        return_attention_mask=True
    )

    labels = [data[label] for label in LABELS]

    representation = {
        'input_ids': encoding['input_ids'],
        'attention_mask': encoding['attention_mask'],
        'labels': torch.FloatTensor(labels)
    }

    return representation

Try natin kung nagana nang maayos ang encode_data function

In [13]:
encode_data(sample_data)   

{'input_ids': tensor([  101,  2222,  1894,  1742,  7178,  8332,   115, 22998,  1894,  1839,
         19451,  1894,   117, 21969,   116, 15357,  1894,  1741,  6627,  2913,
         19451,   117,   102,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,   

Nagana siya so gamitin natin siya para iencode lahat ng data sa isang set
- Goal natin dito magreturn ng isang panibagong dictionary na naglalaman ng encoded sets
- Para iencode ang bawat set, gamitin natin yung loop

In [11]:
encoded_dataset = {}   # mag-initialize ng new dictionary, dito natin ipapasok ang new sets

for key, set in tqdm(raw_dataset.items()): # sa bawat set na meron sa dataset (train, test, val)

    encoded_dataset[key] = [] # initialize a new list, dito natin ipapasok ang encoded sentences
    
    for index, data in set.iterrows(): # sa bawat data sa loob ng isang set (yung hate speech na may labels)
       encoded_dataset[key].append(encode_data(data))

    print(f'{key} set has been encoded')


 33%|███▎      | 1/3 [00:00<00:01,  1.22it/s]

train set has been encoded


100%|██████████| 3/3 [00:01<00:00,  2.36it/s]

test set has been encoded
val set has been encoded


In [15]:
# Eto na yung new set na ready na gamitin for training
encoded_dataset

{'train': [{'input_ids': tensor([  101,  2222,  1894,  1742,  7178,  8332,   115, 22998,  1894,  1839,
           19451,  1894,   117, 21969,   116, 15357,  1894,  1741,  6627,  2913,
           19451,   117,   102,     0,     0,     0,     0,     0,     0,     0,
               0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
               0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
               0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
               0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
               0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
               0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
               0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
               0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
               0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
      

Similarly, tulad ng raw dataset, pwede natin gamitin yung ginawa natin kanina para maaccess ang laman ng encoded dataset

In [16]:
encoded_dataset['train'][0]

"""
['train'] ang key ng set
[0] ang index ng data sa loob ng set

"""

"\n['train'] ang key ng set\n[0] ang index ng data sa loob ng set\n\n"

In [12]:
sample_ids = encoded_dataset['train'][0]['input_ids']
sample_ids

tensor([[  101,  6754,  6144, 12301,  1120, 46109,  1738,  1762, 22998,  1738,
          2578,   167,  5489,  1109,  9272, 20387,  5424,   102,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,  

In [13]:
sample_attention_mask = encoded_dataset['train'][0]['attention_mask']
sample_attention_mask

tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0]])

In [14]:
sample_labels = encoded_dataset['train'][0]['labels']
sample_labels

tensor([1., 0., 0., 0., 0., 0.])

Ganito itsura ng tokens btw

In [16]:
sample_tokens = tokenizer.convert_ids_to_tokens(sample_ids)
print(sample_tokens)


ValueError: only one element tensors can be converted to Python scalars

### Ganto naman magconvert ng y_pred/y_true to actual labels 

In [19]:
id2label = {idx:label for idx, label in enumerate(LABELS)}
label2id = {label:idx for idx, label in enumerate(LABELS)}

In [17]:
y_true = encoded_dataset['train'][0]['labels']
y_true

tensor([1., 0., 0., 0., 0., 0.])

In [18]:
threshold = 0.5
predicted_labels = [label for label, value in zip(LABELS, y_true.int()) if value == 1]

"""
Eto ay isang list comprehension kung saan gumagamit siya ng condition (value == 1) para idetermine kung existing yung label
Nilloop niya ang bawat probabilities sa y_true para makuha ang labels

"""

predicted_labels

['Age']

In [19]:
import pandas as pd
import torch
from torch.utils.data import Dataset, DataLoader
from tqdm import tqdm

raw_dataset = {
    'train': pd.read_csv('../new-dataset/train_data.csv').reset_index(drop=True),
    'test': pd.read_csv('../new-dataset/test_data.csv').reset_index(drop=True),
    'val': pd.read_csv('../new-dataset/val_data.csv').reset_index(drop=True)
}

class MLTHSDataset(Dataset):
    def __init__(self, data, tokenizer, labels, max_token_len=128):
        self.data = data
        self.tokenizer = tokenizer
        self.labels = labels
        self.max_token_len = max_token_len
        self.encoded_dataset = self.encode_dataset()

    def __len__(self):
        return len(self.data)

    def __getitem__(self, index):
        return self.encoded_dataset[index]

    def encode_dataset(self):
        encoded_dataset = []
        for index, data in tqdm(self.data.iterrows()):
            encoded_data = self.encode_data(data)
            encoded_dataset.append(encoded_data)
        return encoded_dataset

    def encode_data(self, data):
        text = data["Text"]
        encoding = self.tokenizer.encode_plus(
            text,
            add_special_tokens=True,
            return_tensors='pt',
            padding='max_length',
            truncation=True,
            max_length=128,
            return_token_type_ids=False,
            return_attention_mask=True
        )
        labels = [data[label] for label in self.labels]
        representation = {
            'input_ids': encoding['input_ids'].flatten(),
            'attention_mask': encoding['attention_mask'].flatten(),
            'labels': torch.FloatTensor(labels)
        }
        return representation

class MLTHSDataLoader:
    def __init__(self, dataset, labels, tokenizer, batch_size=8, max_token_len=128):
        self.train_dataset = MLTHSDataset(dataset['train'], tokenizer, labels)
        self.val_dataset = MLTHSDataset(dataset['val'], tokenizer, labels)
        self.test_dataset = MLTHSDataset(dataset['test'], tokenizer, labels)
        self.batch_size = batch_size

    def train_dataloader(self):
        return DataLoader(self.train_dataset, batch_size=self.batch_size, num_workers=0, shuffle=True)

    def val_dataloader(self):
        return DataLoader(self.val_dataset, batch_size=self.batch_size, num_workers=0, shuffle=False)

    def test_dataloader(self):
        return DataLoader(self.test_dataset, batch_size=self.batch_size, num_workers=0, shuffle=False)

In [45]:
import torch
import torch.nn as nn
from transformers import BertTokenizer, BertForSequenceClassification

tokenizer = BertTokenizer.from_pretrained('gklmip/bert-tagalog-base-uncased')

In [20]:

LABELS = ['Age', 'Gender', 'Physical', 'Race', 'Religion', 'Others']
dataloader = MLTHSDataLoader(dataset=raw_dataset, tokenizer=tokenizer, labels=LABELS)
train_dataloader = dataloader.train_dataloader()
val_dataloader = dataloader.val_dataloader()
test_dataloader = dataloader.test_dataloader()

0it [00:00, ?it/s]

1260it [00:00, 1613.55it/s]
210it [00:00, 1506.24it/s]
630it [00:00, 1746.97it/s]


In [48]:
class_counts = torch.zeros(len(LABELS))
for batch in train_dataloader:
    labels = batch['labels']
    class_counts += labels.sum(dim=0)

# Calculate class weights
total_samples = class_counts.sum()
class_weights = total_samples / (len(LABELS) * class_counts)

# Normalize weights so that the sum is equal to the number of classes
class_weights /= class_weights.sum()

print("Class Weights:", class_weights)

Class Weights: tensor([0.1733, 0.1538, 0.1304, 0.1598, 0.1919, 0.1910])


In [21]:
for batch in train_dataloader:
    print("Input IDs:", batch['input_ids'])
    print("Attention Mask:", batch['attention_mask'])
    print("Labels:", batch['labels'])

    break


"""
This code prints a single batch in the train loader. Since ang batch size ay 8, that means merong 8 rows per batch 

"""

Input IDs: tensor([[  101,  2228,  2074,  ...,     0,     0,     0],
        [  101,  1749,  9689,  ...,     0,     0,     0],
        [  101, 40044,  2309,  ...,     0,     0,     0],
        ...,
        [  101,  1749, 31518,  ...,     0,     0,     0],
        [  101,  2174,  9326,  ...,     0,     0,     0],
        [  101,  9579,   115,  ...,     0,     0,     0]])
Attention Mask: tensor([[1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        ...,
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0]])
Labels: tensor([[0., 1., 1., 0., 0., 0.],
        [0., 0., 0., 0., 1., 0.],
        [0., 1., 0., 0., 0., 0.],
        [1., 0., 0., 0., 0., 0.],
        [1., 0., 0., 0., 0., 0.],
        [0., 0., 1., 1., 0., 0.],
        [0., 1., 0., 0., 0., 0.],
        [0., 0., 1., 0., 0., 0.]])


'\nThis code prints a single batch in the train loader. Since ang batch size ay 8, that means merong 8 rows per batch \n\n'

In [22]:
from transformers import BertModel

In [27]:
LABELS = ['Age', 'Gender', 'Physical', 'Race', 'Religion', 'Others']
model_name = "gklmip/bert-tagalog-base-uncased"

Some weights of BertModel were not initialized from the model checkpoint at gklmip/bert-tagalog-base-uncased and are newly initialized: ['bert.pooler.dense.weight', 'bert.pooler.dense.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [28]:
class HateSpeechClassifier(nn.Module):
    def __init__(self, model_name, num_labels):
        super(HateSpeechClassifier, self).__init__()
        self.bert_model = BertModel.from_pretrained(model_name)
        self.dropout = nn.Dropout(0.1)
        self.linear = nn.Linear(self.bert_model.config.hidden_size, num_labels)

    def forward(self, ids, mask):
        bert_outputs = self.bert_model(ids, attention_mask=mask)
        cls_hidden_state = bert_outputs.last_hidden_state[:, 0, :] 
        dropped_out = self.dropout(cls_hidden_state)
        logits = self.linear(dropped_out)
        return logits

Setup the classifier 

In [29]:
hsclassifier = HateSpeechClassifier(model_name, len(LABELS))
hsclassifier

Some weights of BertModel were not initialized from the model checkpoint at gklmip/bert-tagalog-base-uncased and are newly initialized: ['bert.pooler.dense.weight', 'bert.pooler.dense.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


HateSpeechClassifier(
  (bert_model): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(52099, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, el

### Setup the loss function and optimizer

Ang purpose ng loss function ay para icalculate ang difference between models' prediction and true labels/targets

Ang loss ay something na gusto nating mabawasan sa pamamagitan ng pagtetrain ng model, ito ay ibabackpropagate natin where icacalculate ang gradient of loss ng bawat model's parameters

Optimizer naman ang gagamitin natin to actually update the model's parameters 

In [49]:
criterion = nn.BCEWithLogitsLoss(reduction='mean', weight=class_weights)
optimizer = torch.optim.Adam(hsclassifier.parameters(),lr=2e-5, weight_decay=0.01)

def loss_fn(outputs, targets):
    return criterion(outputs, targets)

print(criterion)
print(optimizer)

BCEWithLogitsLoss()
Adam (
Parameter Group 0
    amsgrad: False
    betas: (0.9, 0.999)
    capturable: False
    differentiable: False
    eps: 1e-08
    foreach: None
    fused: None
    lr: 2e-05
    maximize: False
    weight_decay: 0.01
)


In [31]:
epochs = 5
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
hsclassifier.to(device)

HateSpeechClassifier(
  (bert_model): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(52099, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, el

In [32]:
hsclassifier.train()

HateSpeechClassifier(
  (bert_model): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(52099, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, el

In [55]:
import numpy as np
from sklearn.metrics import multilabel_confusion_matrix
from transformers import EvalPrediction
import torch

def calculate_metrics(confusion_matrix):
    TP = confusion_matrix[1, 1]  # True Positives
    FP = confusion_matrix[0, 1]  # False Positives
    FN = confusion_matrix[1, 0]  # False Negatives
    TN = confusion_matrix[0, 0]  # True Negatives

    precision = TP / (TP + FP) if TP + FP > 0 else 0
    recall = TP / (TP + FN) if TP + FN > 0 else 0
    f1_score = (2 * precision * recall) / (precision + recall) if precision + recall > 0 else 0

    return {
        "Precision": precision,
        "Recall": recall,
        "F1-Score": f1_score
    }

def multilabel_metrics(predictions, labels, threshold=0.5):
    sigmoid = torch.nn.Sigmoid()
    probabilities = sigmoid(torch.Tensor(predictions))

    y_pred = np.zeros(probabilities.shape)
    y_pred[np.where(probabilities >= threshold)] = 1

    y_true = np.zeros(labels.shape)
    y_true[np.where(labels == 1)] = 1

    confusion_matrix = multilabel_confusion_matrix(y_true, y_pred)

    label_metrics = {}
    classes = ['Age', 'Gender', 'Physical', 'Race', 'Religion', 'Others']

    for i, class_name in enumerate(classes):
        metrics = calculate_metrics(confusion_matrix[i])
        label_metrics[class_name] = metrics

        precision = metrics['Precision'] * 100
        recall = metrics['Recall'] * 100
        f1 = metrics['F1-Score'] * 100

        print(f"{class_name}")
        print(f"    Precision: {precision:.2f}%")
        print(f"    Recall: {recall:.2f}%")
        print(f"    F-Measure: {f1:.2f}%")

    xor_result = np.logical_xor(y_true, y_pred)
    xor_sum = np.sum(xor_result)
    hamming_loss = xor_sum / (y_true.shape[0] * y_true.shape[1])
    label_metrics['hamming_loss'] = 1 - hamming_loss

    print("\nHamming Loss:", label_metrics['hamming_loss'])

    return label_metrics

def compute_metrics(p: EvalPrediction):
    preds = p.predictions[0] if isinstance(p.predictions, tuple) else p.predictions
    result = multilabel_metrics(predictions=preds, labels=p.label_ids, threshold=0.5)
    return result

In [45]:
def eval_model(model, dataloader):
    model.eval()
    total_loss = 0.0
    predictions = []
    labels = []

    with torch.no_grad():
        for batch in tqdm(dataloader):
            input_ids = batch['input_ids']
            attention_mask = batch['attention_mask']
            labels = batch['labels']

            outputs = model(input_ids, attention_mask)
            loss = criterion(outputs, labels)
            total_loss += loss.item()

            predictions.append(outputs.cpu().numpy())
            labels.append(labels.cpu().numpy())

    predictions = np.vstack(predictions)
    labels = np.vstack(labels)
    metrics = multilabel_metrics(predictions=predictions, labels=labels, threshold=0.5)

    average_loss = total_loss / len(dataloader)
    return average_loss, metrics

In [53]:
def train_model(model, epochs = 5):

    best_val_loss = float('inf')
        
    for epoch in tqdm(range(1, epoch+1)):    

        model.train()
        total_loss = 0.0

        for batch in train_dataloader:
            input_ids = batch['input_ids']
            attention_mask = batch['attention_mask']
            labels = batch['labels']

            # forward pass
            outputs = model(input_ids, attention_mask)
            loss = loss_fn(outputs, labels)
            print(loss.item())

            # backpropagation
            optimizer.zero_grad(set_to_none=True)
            loss.backward()
            nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)

            # gradient descent (update the model's parameters)
            optimizer.step()

    print(f"Epoch {epochs}, Average Loss: {total_loss / len(train_dataloader)}")

    # Evaluate using validation set, dito natin malalaman kung nag-iimprove ang model
    # Ineexpect natin na dapat bumaba ang loss for each epoch 

    val_loss, val_metrics = eval_model(model, val_dataloader)
    print(f"Validation Loss: {val_loss}")
    print("Validation Metrics:", val_metrics)


In [ ]:
history = {}

trained_model = train_model(epochs=5)


In [50]:
input_ids = encoded_dataset['train'][0]['input_ids']
attention_mask = encoded_dataset['train'][0]['attention_mask']
outputs = hsclassifier(input_ids, attention_mask)
outputs

tensor([[-3.2995, -4.1296, -0.5973, -2.3115, -3.3767, -1.5109]],
       grad_fn=<AddmmBackward0>)

In [ ]:
from transformers import BertModel, BertTokenizer
import torch

# Load pre-trained BERT model and tokenizer
model_name = "gklmip/bert-tagalog-base-uncased"
tokenizer = BertTokenizer.from_pretrained(model_name)
bert_model = BertModel.from_pretrained(model_name)

In [112]:
input_text = "Parang mga ewan ang mga animal sa kanto muntanga"

# Tokenize input text
tokens = tokenizer(input_text, return_tensors="pt")

# Obtain BERT output
output = bert_model(**tokens) 

# check output[0][:,0,:] == cls_hs

""" 
returns last_hidden_state and pooler_output
pooler_output lang kailangan natin kasi eto ay ang cls

"""


' \nreturns last_hidden_state and pooler_output\npooler_output lang kailangan natin kasi eto ay ang cls\n\n'

In [130]:
output

BaseModelOutputWithPoolingAndCrossAttentions(last_hidden_state=tensor([[[-0.1990,  0.4222,  1.2110,  ..., -0.5052,  0.0444, -0.4628],
         [ 0.2340, -0.5906,  1.0896,  ..., -0.5016,  0.3257,  0.3993],
         [ 0.2533,  1.4534, -0.1732,  ..., -0.2475,  0.0156, -0.7223],
         ...,
         [ 0.5575,  0.6763,  0.8881,  ..., -1.3185, -0.3211, -0.3079],
         [-0.3293, -0.9545,  1.0679,  ..., -0.8194, -0.8511,  0.0535],
         [-0.8328, -0.1019,  0.2909,  ..., -0.5112,  0.3095, -0.2303]]],
       grad_fn=<NativeLayerNormBackward0>), pooler_output=tensor([[-3.3992e-01, -2.8852e-01, -3.6100e-01, -2.7696e-01,  5.5344e-01,
          2.5875e-01, -5.1486e-01, -4.7448e-01, -3.0124e-01,  5.2195e-01,
         -3.1555e-01,  3.6567e-01,  7.2461e-02,  1.8094e-01, -5.3699e-01,
         -4.2657e-01,  3.3642e-01,  4.2290e-01, -1.3738e-01,  5.0373e-01,
          5.2732e-01,  2.7478e-04, -2.4375e-01,  3.6180e-01,  3.1174e-01,
          6.2235e-01, -4.1930e-01, -5.4821e-01,  1.4143e-01,  2.248

In [134]:
print(output.last_hidden_state.shape)
print(output.last_hidden_state[:, 0, :].shape) # Ito yung CLS embedding na ipapasok natin sa classifier
print(output.pooler_output.shape)

torch.Size([1, 12, 768])
torch.Size([1, 768])
torch.Size([1, 768])


In [51]:
cls_hs  = output.last_hidden_state[:, 0, :]
cls_hs

NameError: name 'output' is not defined

In [158]:
cls_hidden_state = output.last_hidden_state[:, 0, :] 
logits = fcl(cls_hidden_state)

logits

tensor([[-0.7852,  0.6337,  0.0497, -0.2603, -0.7321,  0.3787]],
       grad_fn=<AddmmBackward0>)

In [171]:
print(f'y_true: {sample_labels}')
print(f'y_pred: {logits.squeeze().detach()}') # squeeze para matanggal yung extra dimension (from [1, 6] to [6])

y_true: tensor([1., 0., 0., 0., 0., 0.])
y_pred: tensor([-0.7852,  0.6337,  0.0497, -0.2603, -0.7321,  0.3787])


In [52]:
loss = nn.BCEWithLogitsLoss(reduction='mean')(outputs.squeeze(), sample_labels)

print("Loss:", loss.item())

Loss: 0.6862764358520508


In [198]:
# Apply sigmoid to logits to get probabilities
probabilities = torch.sigmoid(logits)

# Manually calculate binary cross-entropy loss with reduction='mean'
manual_loss = - (sample_labels * torch.log(probabilities.clamp(min=1e-15)) + (1 - sample_labels) * torch.log((1 - probabilities).clamp(min=1e-15)))

# Calculate the mean of the manual loss
manual_loss_mean = manual_loss.mean().item()

# Print the manual loss mean
print("Manual Loss (mean):", manual_loss_mean)
# Print the loss obtained from the criterion
print("Criterion Loss:", loss.item())

Manual Loss (mean): 0.8004956841468811
Criterion Loss: 0.8004958033561707


In [188]:
hsclassifier.optimizer.step()

In [189]:
hsclassifier.optimizer.zero_grad()

In [154]:
model = BertForSequenceClassification.from_pretrained("gklmip/bert-tagalog-base-uncased",
                                                           problem_type="multi_label_classification",
                                                           num_labels=len(LABELS))

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at gklmip/bert-tagalog-base-uncased and are newly initialized: ['bert.pooler.dense.weight', 'classifier.weight', 'bert.pooler.dense.bias', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [157]:
model(encoded_dataset['train'][0]['input_ids'], encoded_dataset['train'][0]['attention_mask'])

SequenceClassifierOutput(loss=None, logits=tensor([[ 0.0558, -0.1651, -0.2283,  0.4482, -0.1942,  0.2271]],
       grad_fn=<AddmmBackward0>), hidden_states=None, attentions=None)

Class Weights: tensor([0.1733, 0.1538, 0.1304, 0.1598, 0.1919, 0.1910])
